# Polarizability by linear response

We compute the polarizability of a Helium atom. The polarizability
is defined as the change in dipole moment
$$
μ = ∫ r ρ(r) dr
$$
with respect to a small uniform electric field $E = -x$.

We compute this in two ways: first by finite differences (applying a
finite electric field), then by linear response. Note that DFTK is
not really adapted to isolated atoms because it uses periodic
boundary conditions. Nevertheless we can simply embed the Helium
atom in a large enough box (although this is computationally wasteful).

As in other tests, this is not fully converged, convergence
parameters were simply selected for fast execution on CI,

In [1]:
using DFTK
using LinearAlgebra

a = 10.
lattice = a * I(3)  # cube of $a$ bohrs
# Helium at the center of the box
atoms     = [ElementPsp(:He, psp=load_psp("hgh/lda/He-q2"))]
positions = [[1/2, 1/2, 1/2]]


kgrid = [1, 1, 1]  # no k-point sampling for an isolated system
Ecut = 30
tol = 1e-8

# dipole moment of a given density (assuming the current geometry)
function dipole(basis, ρ)
    rr = [(r[1] - a/2) for r in r_vectors_cart(basis)]
    sum(rr .* ρ) * basis.dvol
end;

## Using finite differences
We first compute the polarizability by finite differences.
First compute the dipole moment at rest:

In [2]:
model = model_LDA(lattice, atoms, positions; symmetries=false)
basis = PlaneWaveBasis(model; Ecut, kgrid)
res   = self_consistent_field(basis; tol)
μref  = dipole(basis, res.ρ)

n     Energy            log10(ΔE)   log10(Δρ)   Diag   Δtime
---   ---------------   ---------   ---------   ----   ------
  1   -2.770166128320                   -0.53    8.0         
  2   -2.771671638499       -2.82       -1.30    1.0    166ms
  3   -2.771713080618       -4.38       -2.69    1.0    120ms
  4   -2.771714708451       -5.79       -3.69    2.0    171ms
  5   -2.771714714230       -8.24       -4.07    2.0    162ms
  6   -2.771714715233       -9.00       -5.45    1.0    125ms
  7   -2.771714715250      -10.78       -5.89    2.0    148ms
  8   -2.771714715250      -13.08       -6.38    1.0    132ms
  9   -2.771714715250      -13.78       -7.15    2.0    164ms
 10   -2.771714715250   +  -14.35       -7.43    1.0    139ms
 11   -2.771714715250      -14.27       -8.42    1.0    142ms


-0.00013457222589843688

Then in a small uniform field:

In [3]:
ε = .01
model_ε = model_LDA(lattice, atoms, positions;
                    extra_terms=[ExternalFromReal(r -> -ε * (r[1] - a/2))],
                    symmetries=false)
basis_ε = PlaneWaveBasis(model_ε; Ecut, kgrid)
res_ε   = self_consistent_field(basis_ε; tol)
με = dipole(basis_ε, res_ε.ρ)

n     Energy            log10(ΔE)   log10(Δρ)   Diag   Δtime
---   ---------------   ---------   ---------   ----   ------
  1   -2.770506692333                   -0.52    9.0         
  2   -2.771779147540       -2.90       -1.33    1.0    148ms
  3   -2.771801594188       -4.65       -2.42    1.0    142ms
  4   -2.771802002591       -6.39       -3.13    1.0    180ms
  5   -2.771802074346       -7.14       -4.66    2.0    144ms
  6   -2.771802074462       -9.93       -4.75    2.0    165ms
  7   -2.771802074475      -10.88       -5.82    1.0    128ms
  8   -2.771802074476      -12.10       -6.08    2.0    151ms
  9   -2.771802074476      -13.43       -6.97    1.0    149ms
 10   -2.771802074476      -14.18       -7.43    2.0    170ms
 11   -2.771802074476   +  -13.83       -8.67    1.0    134ms


0.017612221444500042

In [4]:
polarizability = (με - μref) / ε

println("Reference dipole:  $μref")
println("Displaced dipole:  $με")
println("Polarizability :   $polarizability")

Reference dipole:  -0.00013457222589843688
Displaced dipole:  0.017612221444500042
Polarizability :   1.774679367039848


The result on more converged grids is very close to published results.
For example [DOI 10.1039/C8CP03569E](https://doi.org/10.1039/C8CP03569E)
quotes **1.65** with LSDA and **1.38** with CCSD(T).

## Using linear response
Now we use linear response to compute this analytically; we refer to standard
textbooks for the formalism. In the following, $χ_0$ is the
independent-particle polarizability, and $K$ the
Hartree-exchange-correlation kernel. We denote with $δV_{\rm ext}$ an external
perturbing potential (like in this case the uniform electric field). Then:
$$
δρ = χ_0 δV = χ_0 (δV_{\rm ext} + K δρ),
$$
which implies
$$
δρ = (1-χ_0 K)^{-1} χ_0 δV_{\rm ext}.
$$
From this we identify the polarizability operator to be $χ = (1-χ_0 K)^{-1} χ_0$.
Numerically, we apply $χ$ to $δV = -x$ by solving a linear equation
(the Dyson equation) iteratively.

In [5]:
using KrylovKit

# Apply $(1- χ_0 K)$
function dielectric_operator(δρ)
    δV = apply_kernel(basis, δρ; res.ρ)
    χ0δV = apply_χ0(res, δV)
    δρ - χ0δV
end

# `δVext` is the potential from a uniform field interacting with the dielectric dipole
# of the density.
δVext = [-(r[1] - a/2) for r in r_vectors_cart(basis)]
δVext = cat(δVext; dims=4)

# Apply $χ_0$ once to get non-interacting dipole
δρ_nointeract = apply_χ0(res, δVext)

# Solve Dyson equation to get interacting dipole
δρ = linsolve(dielectric_operator, δρ_nointeract, verbosity=3)[1]

println("Non-interacting polarizability: $(dipole(basis, δρ_nointeract))")
println("Interacting polarizability:     $(dipole(basis, δρ))")

[ Info: GMRES linsolve in iter 1; step 1: normres = 2.493920760975e-01
[ Info: GMRES linsolve in iter 1; step 2: normres = 3.766551112126e-03
[ Info: GMRES linsolve in iter 1; step 3: normres = 2.852756867970e-04
[ Info: GMRES linsolve in iter 1; step 4: normres = 4.694594596222e-06
[ Info: GMRES linsolve in iter 1; step 5: normres = 1.088791605039e-08
[ Info: GMRES linsolve in iter 1; step 6: normres = 6.307205114081e-11
[ Info: GMRES linsolve in iter 1; step 7: normres = 1.535530211163e-12
[ Info: GMRES linsolve in iter 1; finished at step 7: normres = 1.535530211163e-12
[ Info: GMRES linsolve in iter 2; step 1: normres = 9.701963585317e-11
[ Info: GMRES linsolve in iter 2; step 2: normres = 9.955267745767e-13
[ Info: GMRES linsolve in iter 2; finished at step 2: normres = 9.955267745767e-13
┌ Info: GMRES linsolve converged at iteration 2, step 2:
│ *  norm of residual = 9.955407214208665e-13
└ *  number of operations = 11
Non-interacting polarizability: 1.925712541802577
Interacting

As expected, the interacting polarizability matches the finite difference
result. The non-interacting polarizability is higher.